In [1]:
from configparser import ConfigParser
import psycopg2
import pandas as pd
import os


In [2]:

def load_config(filename='database.ini', section='postgresql'):
    current_dir = os.path.dirname(os.path.abspath(__file__)) if '__file__' in globals() else os.getcwd()
    file_path = os.path.join(current_dir, filename)

    if not os.path.exists(file_path):
        raise Exception(f"File {file_path} not found")

    parser = ConfigParser()
    parser.read(file_path)

    config = {}
    if parser.has_section(section):
        params = parser.items(section)
        for param in params:
            config[param[0]] = param[1]
    else:
        sections = parser.sections()
        raise Exception(f"Section {section} not found in {file_path}. Available sections: {sections}")

    return config


In [3]:
def connect(config):
    """Kết nối tới PostgreSQL và trả về đối tượng connection"""
    conn = None
    try:
        conn = psycopg2.connect(**config)
        print("✅ Connected to PostgreSQL server.")
        return conn
    except (Exception, psycopg2.DatabaseError) as error:
        print(f"❌ Error connecting to database: {error}")
        return None


In [4]:
config = load_config()
conn = connect(config)


conn.autocommit = True
cursor = conn.cursor()


✅ Connected to PostgreSQL server.


In [44]:
#  Tạo bảng dim_stadium
sql1 = '''
CREATE TABLE IF NOT EXISTS Dim_Stadium (
    stadium_id INT PRIMARY KEY,
    stadium_name VARCHAR(255) NOT NULL,
    capacity INT
);
'''
cursor.execute(sql1)

#  Nạp dữ liệu từ CSV
with open(r'D:\ETL_football\data_processed\dim_stadium.csv', 'r') as f:
    cursor.copy_expert("""
        COPY Dim_Stadium(stadium_id, stadium_name, capacity)
        FROM STDIN
        WITH (FORMAT CSV, DELIMITER ',', HEADER TRUE)
    """, f)

# Kiểm tra kết quả
cursor.execute('SELECT * FROM Dim_Stadium;')
for row in cursor.fetchall():
    print(row)


(619094, 'Dean Court', 12000)
(163995, 'Emirates Stadium', 60338)
(175339, 'Villa Park', 42640)
(1546623, 'Gtech Community Stadium', 17250)
(619409, 'Brighton Community Stadium', 31800)
(171458, 'Stamford Bridge', 41875)
(1066373, 'Selhurst Park', 26255)
(188874, 'Goodison Park', 39414)
(318043, 'Craven Cottage', 25700)
(619558, 'Portman Road', 30311)
(620031, 'King Power Stadium', 32261)
(45671, 'Anfield', 53394)
(48159, 'Etihad Stadium', 55017)
(83457, 'Old Trafford', 75731)
(191774, 'St Jamesâ€™ Park', 52305)
(593446, 'City Ground', 30404)
(567339, "St Mary's Stadium", 32589)
(55074091, 'Tottenham Hotspur Stadium', 62850)
(172190, 'London Stadium', 62500)
(380823, 'Molineux Stadium', 30852)
(245085, 'Ewood Park', 31367)
(726370, 'Ashton Gate Stadium', 27699)
(683112, 'Turf Moor', 21944)
(503848, 'Cardiff City Stadium', 33280)
(842077, 'Coventry Building Society Arena', 32609)
(201612, 'Pride Park Stadium', 33597)
(630160, 'MKM Stadium', 25400)
(619505, 'Elland Road', 37792)
(1063683

In [45]:
#  Tạo bảng Dim_team
sql1 = '''
CREATE TABLE IF NOT EXISTS Dim_Team (
    team_id INT PRIMARY KEY,
    team_name VARCHAR(255) NOT NULL, 
    founded_year INT, 
    stadium_id INT,
    shot_name VARCHAR(20),
    FOREIGN KEY (stadium_id) REFERENCES Dim_Stadium(stadium_id)
);
'''
cursor.execute(sql1)

#  Nạp dữ liệu từ CSV
with open(r'D:\ETL_football\data_processed\dim_team.csv', 'r') as f:
    cursor.copy_expert("""
        COPY Dim_team(team_id,team_name,founded_year,stadium_id,shot_name)
        FROM STDIN
        WITH (FORMAT CSV, DELIMITER ',', HEADER TRUE)
    """, f)

# Kiểm tra kết quả
cursor.execute('SELECT * FROM Dim_Stadium;')
for row in cursor.fetchall():
    print(row)

(619094, 'Dean Court', 12000)
(163995, 'Emirates Stadium', 60338)
(175339, 'Villa Park', 42640)
(1546623, 'Gtech Community Stadium', 17250)
(619409, 'Brighton Community Stadium', 31800)
(171458, 'Stamford Bridge', 41875)
(1066373, 'Selhurst Park', 26255)
(188874, 'Goodison Park', 39414)
(318043, 'Craven Cottage', 25700)
(619558, 'Portman Road', 30311)
(620031, 'King Power Stadium', 32261)
(45671, 'Anfield', 53394)
(48159, 'Etihad Stadium', 55017)
(83457, 'Old Trafford', 75731)
(191774, 'St Jamesâ€™ Park', 52305)
(593446, 'City Ground', 30404)
(567339, "St Mary's Stadium", 32589)
(55074091, 'Tottenham Hotspur Stadium', 62850)
(172190, 'London Stadium', 62500)
(380823, 'Molineux Stadium', 30852)
(245085, 'Ewood Park', 31367)
(726370, 'Ashton Gate Stadium', 27699)
(683112, 'Turf Moor', 21944)
(503848, 'Cardiff City Stadium', 33280)
(842077, 'Coventry Building Society Arena', 32609)
(201612, 'Pride Park Stadium', 33597)
(630160, 'MKM Stadium', 25400)
(619505, 'Elland Road', 37792)
(1063683

In [46]:
#  Tạo bảng dim match
sql1 = '''
CREATE TABLE IF NOT EXISTS Dim_match (
    game_id INT PRIMARY KEY,
    game  VARCHAR(255) NOT NULL, 
    game_date date
);
'''
cursor.execute(sql1)

#  Nạp dữ liệu từ CSV
with open(r'D:\ETL_football\data_processed\dim_match.csv', 'r') as f:
    
    
    cursor.copy_expert("""
        COPY Dim_match(game_id, game, game_date)
        FROM STDIN
               WITH CSV DELIMITER ',' HEADER; 

    """, f)
# Kiểm tra kết quả
cursor.execute('SELECT * FROM Dim_match;')
for row in cursor.fetchall():
    print(row)

(1, '2020-09-12 Fulham-Arsenal', datetime.date(2020, 9, 12))
(2, '2020-09-12 Liverpool-Leeds United', datetime.date(2020, 9, 12))
(3, '2020-09-12 West Ham-Newcastle Utd', datetime.date(2020, 9, 12))
(4, '2020-09-12 Crystal Palace-Southampton', datetime.date(2020, 9, 12))
(5, '2020-09-13 West Brom-Leicester City', datetime.date(2020, 9, 13))
(6, '2020-09-13 Tottenham-Everton', datetime.date(2020, 9, 13))
(7, '2020-09-14 Sheffield Utd-Wolves', datetime.date(2020, 9, 14))
(8, '2020-09-14 Brighton-Chelsea', datetime.date(2020, 9, 14))
(9, '2020-09-19 Arsenal-West Ham', datetime.date(2020, 9, 19))
(10, '2020-09-19 Everton-West Brom', datetime.date(2020, 9, 19))
(11, '2020-09-19 Leeds United-Fulham', datetime.date(2020, 9, 19))
(12, '2020-09-19 Manchester Utd-Crystal Palace', datetime.date(2020, 9, 19))
(13, '2020-09-20 Leicester City-Burnley', datetime.date(2020, 9, 20))
(14, '2020-09-20 Southampton-Tottenham', datetime.date(2020, 9, 20))
(15, '2020-09-20 Newcastle Utd-Brighton', datetime.d

In [47]:
#  Tạo bảng dim_player
sql1 = '''
CREATE TABLE IF NOT EXISTS Dim_player (
    player_id INT PRIMARY KEY,
    player_name  VARCHAR(255) NOT NULL, 
    pos CHAR(10),
    nation VARCHAR(20),
    born INT
);
'''
cursor.execute(sql1)

#  Nạp dữ liệu từ CSV
with open(r'D:\ETL_football\data_processed\dim_player.csv', 'r', encoding='utf-8') as f:
    cursor.copy_expert("""
        COPY Dim_player(player_id, player_name, pos, nation, born)
        FROM STDIN
        WITH (
            FORMAT CSV,
            DELIMITER ',',
            HEADER TRUE
        );
    """, f)
# Kiểm tra kết quả
cursor.execute('SELECT * FROM Dim_player;')
for row in cursor.fetchall():
    print(row)

(1, 'Alexandre Lacazette', 'FW        ', 'FRA', 1991)
(2, 'Bernd Leno', 'GK        ', 'GER', 1992)
(3, 'Bukayo Saka', 'FW,MF     ', 'ENG', 2001)
(4, 'Calum Chambers', 'DF        ', 'ENG', 1995)
(5, 'Cédric Soares', 'DF        ', 'POR', 1991)
(6, 'Dani Ceballos', 'MF        ', 'ESP', 1996)
(7, 'David Luiz', 'DF        ', 'BRA', 1987)
(8, 'Eddie Nketiah', 'FW        ', 'ENG', 1999)
(9, 'Emile Smith Rowe', 'MF,FW     ', 'ENG', 2000)
(10, 'Gabriel Magalhães', 'DF        ', 'BRA', 1997)
(11, 'Gabriel Martinelli', 'FW        ', 'BRA', 2001)
(12, 'Granit Xhaka', 'MF,DF     ', 'SUI', 1992)
(13, 'Héctor Bellerín', 'DF,MF     ', 'ESP', 1995)
(14, 'Joe Willock', 'MF        ', 'ENG', 1999)
(15, 'Kieran Tierney', 'DF        ', 'SCO', 1997)
(16, 'Martin Ødegaard', 'MF        ', 'NOR', 1998)
(17, 'Mathew Ryan', 'GK        ', 'AUS', 1992)
(18, 'Mohamed Elneny', 'MF        ', 'EGY', 1992)
(19, 'Nicolas Pépé', 'FW        ', 'CIV', 1995)
(20, 'Pablo Marí', 'DF        ', 'ESP', 1993)
(21, 'Pierre-Emerick 

In [48]:
#  Tạo bảng dim_season
sql1 = '''
CREATE TABLE IF NOT EXISTS Dim_season (
    season_id INT PRIMARY KEY,
    season_name VARCHAR(15) UNIQUE,
    start_year INT,
    end_year INT,
    actual_start_date DATE ,
    actual_end_date DATE

);
'''
cursor.execute(sql1)

#  Nạp dữ liệu từ CSV
with open(r'D:\ETL_football\data_processed\dim_season.csv', 'r', encoding='utf-8') as f:
    cursor.copy_expert("""
        COPY Dim_season(season_id,season_name, start_year,end_year,actual_start_date,actual_end_date)
        FROM STDIN
        WITH (
            FORMAT CSV,
            DELIMITER ',',
            HEADER TRUE
        );
    """, f)
# Kiểm tra kết quả
cursor.execute('SELECT * FROM Dim_season;')
for row in cursor.fetchall():
    print(row)

(2021, '2020-2021', 2020, 2021, datetime.date(2020, 9, 12), datetime.date(2021, 5, 23))
(2122, '2021-2022', 2021, 2022, datetime.date(2021, 8, 13), datetime.date(2022, 5, 22))
(2223, '2022-2023', 2022, 2023, datetime.date(2022, 8, 5), datetime.date(2023, 5, 28))
(2324, '2023-2024', 2023, 2024, datetime.date(2023, 8, 11), datetime.date(2024, 5, 19))
(2425, '2024-2025', 2024, 2025, datetime.date(2024, 8, 16), datetime.date(2025, 5, 25))
(2526, '2025-2026', 2025, 2026, datetime.date(2025, 8, 15), datetime.date(2026, 5, 24))


In [49]:
#  Tạo bảng fact_team_match
sql1 = '''
CREATE TABLE fact_team_match (
    season          INT,
    game_id         INT,
    team_id         INT,
    opponent_id     INT,
    round           INT,
    venue           VARCHAR(10),
    result          CHAR(1),
    GF              INT,
    GA              INT,
    xG              NUMERIC(4,2),
    xGA             NUMERIC(4,2),
    Poss            INT,
    captain_id      INT,
    Formation       VARCHAR(20),
    Opp_Formation   VARCHAR(20),

    -- Khóa chính đề xuất
    PRIMARY KEY (season, game_id, team_id),

    -- FOREIGN KEYS
    FOREIGN KEY (season)
        REFERENCES dim_season(season_id),

    FOREIGN KEY (game_id)
        REFERENCES dim_match(game_id),

    FOREIGN KEY (team_id)
        REFERENCES dim_team(team_id),

    FOREIGN KEY (opponent_id)
        REFERENCES dim_team(team_id),

    FOREIGN KEY (captain_id)
        REFERENCES dim_player(player_id)
);

'''
cursor.execute(sql1)

#  Nạp dữ liệu từ CSV
with open(r'D:\ETL_football\data_processed\fact_team_match_clean.csv', 'r', encoding='utf-8') as f:
    cursor.copy_expert("""
        COPY fact_team_match(season,game_id,team_id,opponent_id,round,venue,result,GF,GA,xG,xGA,Poss,captain_id,Formation,Opp_Formation)
        FROM STDIN
        WITH (
            FORMAT CSV,
            DELIMITER ',',
            HEADER TRUE
        );
    """, f)
# Kiểm tra kết quả
cursor.execute('SELECT * FROM fact_team_match;')
for row in cursor.fetchall():
    print(row)

(2021, 1, 9617, 18708, 1, 'Away', 'W', 3, 0, Decimal('1.90'), Decimal('0.10'), 54, 21, '3-4-3', '4-2-3-1')
(2021, 9, 9617, 18747, 2, 'Home', 'W', 2, 1, Decimal('1.10'), Decimal('2.00'), 62, 21, '3-4-3', '5-4-1')
(2021, 28, 9617, 1130849, 3, 'Away', 'L', 1, 3, Decimal('1.30'), Decimal('2.70'), 34, 21, '3-4-3', '4-3-3')
(2021, 37, 9617, 19607, 4, 'Home', 'W', 2, 1, Decimal('0.60'), Decimal('0.20'), 64, 21, '4-3-3', '3-5-2')
(2021, 41, 9617, 50602, 5, 'Away', 'L', 0, 1, Decimal('0.90'), Decimal('1.30'), 42, 21, '4-3-3', '3-1-4-2')
(2021, 56, 9617, 19481, 6, 'Home', 'L', 0, 1, Decimal('0.70'), Decimal('0.70'), 56, 21, '3-4-3', '3-4-3')
(2021, 63, 9617, 18656, 7, 'Away', 'W', 1, 0, Decimal('1.00'), Decimal('0.40'), 46, 21, '3-4-3', '4-1-2-1-2')
(2021, 75, 9617, 18711, 8, 'Home', 'L', 0, 3, Decimal('1.50'), Decimal('1.80'), 59, 21, '3-4-3', '4-2-3-1')
(2021, 84, 9617, 1128631, 9, 'Away', 'D', 0, 0, Decimal('0.90'), Decimal('1.80'), 34, 21, '4-2-3-1', '4-1-4-1')
(2021, 94, 9617, 19500, 10, 'H

In [50]:
#  Tạo bảng fact_player_match
sql1 = '''
CREATE TABLE fact_player_match (
    season                  INT,
    game_id                 INT,
    team_id                 INT,
    player_id               INT,
    
    min_played              INT,
    goals                   INT,
    assists                 INT,
    penalty_made            INT,
    penalty_attempted       INT,
    shots                   INT,
    shots_on_target         INT,
    yellow_cards            INT,
    red_cards               INT,
    touches                 INT,
    tackles                 INT,
    interceptions           INT,
    blocks                  INT,
    shot_creating_actions   INT,
    goal_creating_actions   INT,
    passes_completed        INT,
    passes_attempted        INT,
    pass_completion_percent NUMERIC(5,2),
    progressive_passes      INT,
    carries                 INT,
    progressive_carries     INT,
    take_ons_attempted      INT,
    take_ons_successful     INT,

    -- KHÓA NGOẠI
    FOREIGN KEY (season)      REFERENCES dim_season(season_id),
    FOREIGN KEY (game_id)     REFERENCES dim_match(game_id),
    FOREIGN KEY (team_id)     REFERENCES dim_team(team_id),
    FOREIGN KEY (player_id)   REFERENCES dim_player(player_id)
);


'''
cursor.execute(sql1)

#  Nạp dữ liệu từ CSV
with open(r'D:\ETL_football\data_processed\fact_player_match_clean.csv', 'r', encoding='utf-8') as f:
    cursor.copy_expert("""
        COPY fact_player_match(season,game_id,team_id,player_id,min_played,goals,assists,penalty_made,penalty_attempted,shots,shots_on_target,yellow_cards,red_cards,touches,tackles,interceptions,blocks,shot_creating_actions,goal_creating_actions,passes_completed,passes_attempted,pass_completion_percent,progressive_passes,carries,progressive_carries,take_ons_attempted,take_ons_successful)
        FROM STDIN
        WITH (
            FORMAT CSV,
            DELIMITER ',',
            HEADER TRUE
        );
    """, f)
# Kiểm tra kết quả
cursor.execute('SELECT * FROM fact_player_match;')
for row in cursor.fetchall():
    print(row)

(2021, 4, 19467, 131, 90, 0, 0, 0, 0, 1, 1, 0, 0, 25, 1, 0, 1, 0, 0, 11, 19, Decimal('57.90'), 2, 6, 0, 0, 0)
(2021, 4, 19467, 133, 10, 0, 0, 0, 0, 0, 0, 0, 0, 13, 0, 0, 0, 0, 0, 8, 10, Decimal('80.00'), 2, 11, 1, 5, 2)
(2021, 4, 19467, 136, 90, 0, 0, 0, 0, 1, 0, 0, 0, 45, 2, 3, 0, 2, 0, 15, 32, Decimal('46.90'), 3, 12, 0, 1, 1)
(2021, 4, 19467, 137, 73, 0, 0, 0, 0, 0, 0, 1, 0, 29, 1, 2, 1, 1, 1, 14, 23, Decimal('60.90'), 2, 4, 0, 0, 0)
(2021, 4, 19467, 141, 80, 0, 0, 0, 0, 0, 0, 1, 0, 20, 1, 2, 1, 0, 0, 1, 13, Decimal('7.70'), 1, 9, 1, 0, 0)
(2021, 4, 19467, 142, 90, 0, 0, 0, 0, 0, 0, 0, 0, 45, 0, 1, 0, 0, 0, 23, 37, Decimal('62.20'), 3, 8, 1, 0, 0)
(2021, 4, 19467, 143, 90, 0, 0, 0, 0, 1, 1, 0, 0, 24, 2, 0, 3, 1, 0, 4, 8, Decimal('50.00'), 0, 22, 1, 5, 4)
(2021, 4, 19467, 144, 17, 0, 0, 0, 0, 0, 0, 0, 0, 16, 0, 0, 0, 2, 0, 9, 12, Decimal('75.00'), 1, 3, 0, 0, 0)
(2021, 4, 19467, 150, 90, 0, 0, 0, 0, 0, 0, 0, 0, 38, 0, 2, 0, 0, 0, 14, 27, Decimal('51.90'), 0, 2, 0, 0, 0)
(2021, 4, 194

In [51]:
#  Tạo bảng fact_team_point
sql1 = '''
CREATE TABLE fact_team_point (
    season_id      INT NOT NULL,
    Match_Category VARCHAR(100) NOT NULL,
    Rank           INT NOT NULL,
    team_id        INT NOT NULL,
    MP             INT,
    W              INT,
    D              INT,
    L              INT,
    GF             INT,
    GA             INT,
    GD             INT,
    Pts            INT,
    Recent_Form    VARCHAR(50),

    
    PRIMARY KEY (season_id, team_id, Match_Category),

    FOREIGN KEY (season_id) REFERENCES dim_season(season_id),
    FOREIGN KEY (team_id)   REFERENCES dim_team(team_id)
);

'''
cursor.execute(sql1)

#  Nạp dữ liệu từ CSV
with open(r'D:\ETL_football\data_processed\fact_team_point.csv', 'r', encoding='utf-8') as f:
    cursor.copy_expert("""
        COPY fact_team_point(season_id,Match_Category,Rank,team_id,MP,W,D,L,GF,GA,GD,Pts,Recent_Form)
        FROM STDIN
        WITH (
            FORMAT CSV,
            DELIMITER ',',
            HEADER TRUE
        );
    """, f)
# Kiểm tra kết quả
cursor.execute('SELECT * FROM fact_team_point;')
for row in cursor.fetchall():
    print(row)

(2425, 'overall', 1, 1130849, 38, 25, 9, 4, 86, 41, 45, 84, 'DLDLW')
(2425, 'overall', 2, 9617, 38, 20, 14, 4, 69, 34, 35, 74, 'WWDLD')
(2425, 'overall', 3, 50602, 38, 21, 8, 9, 72, 44, 28, 71, 'WWDWW')
(2425, 'overall', 4, 9616, 38, 20, 9, 9, 64, 43, 21, 69, 'WWLWW')
(2425, 'overall', 5, 18716, 38, 20, 6, 12, 68, 47, 21, 66, 'LLWDW')
(2425, 'overall', 6, 18711, 38, 19, 9, 10, 58, 51, 7, 66, 'LWWWL')
(2425, 'overall', 7, 19490, 38, 19, 8, 11, 58, 46, 12, 65, 'LWDDL')
(2425, 'overall', 8, 19453, 38, 16, 13, 9, 66, 59, 7, 61, 'WWWDW')
(2425, 'overall', 9, 19568, 38, 15, 11, 12, 58, 46, 12, 56, 'WLLWD')
(2425, 'overall', 10, 19571, 38, 16, 8, 14, 66, 57, 9, 56, 'DLWWW')
(2425, 'overall', 11, 18708, 38, 15, 9, 14, 54, 54, 0, 54, 'LWLLW')
(2425, 'overall', 12, 19467, 38, 13, 14, 11, 51, 51, 0, 53, 'DWWDD')
(2425, 'overall', 13, 5794, 38, 11, 15, 12, 42, 44, -2, 48, 'WWWDL')
(2425, 'overall', 14, 18747, 38, 11, 10, 17, 46, 62, -16, 43, 'WLWDL')
(2425, 'overall', 15, 18656, 38, 11, 9, 18, 44,